In [1]:
from tqdm import tqdm
import numpy as np
import pandas as pd
from nltk import word_tokenize
from nltk.tokenize.treebank import TreebankWordDetokenizer

In [2]:
import nltk
nltk.download('punkt')

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\diame\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


True

In [3]:
df = pd.read_csv('Base.csv')

In [4]:
df.head()

Unnamed: 0  indi                                             cuerpo  \
0           0     0  dos semanas después de su puesta de largo y pr...   
1           1     1  este viernes, el presidente del gobierno, pedr...   
2           2     2  el ministro del interior, fernando grande-marl...   
3           3     3  son días muy duros para la familia de olivia y...   
4           4     4  sólo quedan 10 presos de eta por recibir los b...   

                                             titular  
0                         el submarino s-80 ya flota  
1  calviño y calvo alaban (sin darse cuenta) la g...  
2  el geo de la policía tendrá una nueva sede en ...  
3  la madre de las niñas "sobran las palabras par...  
4  sólo quedan 10 presos de eta por recibir el be...

In [5]:
#Vamos a usar solamente la columna "cuerpo"

textos = df['cuerpo']

In [6]:
textos.head()

0    dos semanas después de su puesta de largo y pr...
1    este viernes, el presidente del gobierno, pedr...
2    el ministro del interior, fernando grande-marl...
3    son días muy duros para la familia de olivia y...
4    sólo quedan 10 presos de eta por recibir los b...
Name: cuerpo, dtype: object

In [7]:
# Necesitamos tener en cuenta la palabra anterior y la palabra posterior
# para modificar la del medio. Tenemos que tener en cuenta también la cantidad
# de veces que aparece la palabra del medio

# key: (w(t-1), w(t+1)), value: {w(t): count(w(t))}

probs = {}

In [8]:
#Recorremos aca uno de los textos, separándolos en oraciones:

for doc in tqdm(textos):
    oraciones = doc.split(".")
    for oracion in oraciones:
        tokens = word_tokenize(oracion, language = 'spanish')
        if len(tokens) >= 2: #si la oración tiene dos o más palabras   
            for i in range(len(tokens) - 2):
                t_0 = tokens[i]
                #definimos el token 0 como la palabra anterior a la que queremos hacer el split
                t_1 = tokens[i+1]
                #definimos el token 1 como la palabra que vamos a querer reemplazar
                t_2 = tokens[i+2]
                #token 2 es la siguiente palabra
                #por eso recorremos el arreglo hasta len(tokens) - 2, porque sino
                #daría error al buscar en las últimas dos i. 

                key = (t_0, t_2) #--> las palabras que "rodean"
                if key not in probs:
                    probs[key] = {}
                if t_1 not in probs[key]:
                    probs[key][t_1] = 1
                else:
                    probs[key][t_1] += 1



100%|██████████| 58424/58424 [24:24<00:00, 39.89it/s]  


In [9]:
probs

{('dos', 'después'): {'semanas': 95,
  'años': 283,
  'días': 296,
  'meses': 208,
  'horas': 35,
  'siglos': 4,
  'minutos': 4,
  'décadas': 16,
  'elecciones': 2,
  'día': 3,
  'jornadas': 2,
  'legislaturas': 1,
  'domingos': 1,
  'negocios': 1,
  'pasiones': 1,
  'decenios': 1,
  'iniciativas': 1,
  'dispositivos': 1},
 ('semanas', 'de'): {'después': 135,
  'oficiales': 2,
  'antes': 80,
  'tratando': 4,
  'es': 2,
  'fueron': 3,
  ',': 11,
  'varios': 2,
  'pone': 2,
  'alejados': 2,
  'acaba': 1,
  'multitud': 1,
  'más': 3,
  'proviene': 1,
  'advirtiendo': 3,
  'peticioes': 1,
  'fuera': 1,
  '»': 1,
  'que': 2,
  'uno': 2,
  'y': 3,
  'avisando': 1,
  'seguidas': 2,
  'clave': 1,
  'dos': 1,
  'rodeados': 1,
  'algunas': 1,
  'atrás': 1,
  'encima': 1,
  'informativas': 1,
  'consecutivas': 4,
  'alertando': 3,
  'presidente': 1,
  'acusaciones': 1,
  'previas': 1,
  'adicionales': 3,
  'extra': 2,
  'intensas': 1,
  'socio': 1,
  'armándose': 1,
  'diciendo': 1,
  'exactas': 

In [10]:
#Normalizar probabilidades:

for key, d in probs.items():
    total = sum(d.values())
    for k, v in d.items():
        d[k] = v / total

In [11]:
detokenizar = TreebankWordDetokenizer()

In [12]:
def spin_document(doc):
    lineas = doc.split(".")
    output = []
    for linea in lineas:
        if linea:
            new_line = spin_line(linea)
        else:
            new_line = linea

        output.append(new_line)

    return "\n".join(output)

In [13]:
#definición de la función sample word
#obtenemos una palabra random en base a una probabilidad

def sample_word(diccionario):

    #calculamos una probabilidad random
    p0 = np.random.random()

    #calculamos una probabilidad acumulativa que inicializamos en 0

    cumulative = 0

    for palabra, p in diccionario.items():
        cumulative += p
        if p0 < cumulative:
            return palabra

In [15]:
#definimos función spin_line()

def spin_line(linea):
    tokens = word_tokenize(linea, language="spanish")
    i = 0
    salida = [tokens[0]]

    if len(tokens) >= 2:
        while i < (len(tokens) - 2):
            t_0 = tokens[i]
            t_1 = tokens[i+1]
            t_2 = tokens[i+2]

            key = (t_0, t_2)
            p_dist = probs[key]

            #si hay más de una palabra
            if len(p_dist) > 1 and np.random.random() < 0.3:
                middle = sample_word(p_dist)

                salida.append(t_1)
                salida.append("<" + middle + ">")
                salida.append(t_2)

                i+=2
            else:
                salida.append(t_1)
                i +=1

        if i == len(tokens) - 2:
            salida.append(tokens[-1])

    return detokenizar.detokenize(salida)


In [22]:
print(spin_line("dos días después cómo están"))

dos días <años> después cómo están


In [23]:
i = np.random.choice(textos.shape[0])

doc = textos.iloc[i]
new_doc = spin_document(doc)

In [24]:
new_doc

'alberto núñez feijóo es el <el> candidato preferido <elegido> por las <las> bases del pp <año> para suceder a mariano rajoy <rajoy>, porque ofrece <,> esa cara amable y joven de gestor <ser> modélico que da <en> tan bien en los telediarios estatales y que la mayoría de militantes y simpatizantes consideran fundamental para emprender <cumplir> la renovación del partido\nfeijóo se les aparece en <en> las antípodas de rajoy <empleo> y de <a> la asociación que buena <formaba> parte de la opinión pública <"> hace del nombre <juzgado> del expresidente <ministerio> del gobierno con la corrupción y las políticas antisociales\ny a simple vista feijóo sale bien en <de> la comparación\npero el dibujo que <en> el presidente <nombre> de la <la> xunta ha <ha> hecho de su propia imagen para venderse <presentarse> como reemplazo <telón> de rajoy dista mucho del que se desprende del análisis de los <los> resultados de su <la> acción política en <desde> galicia\nfeijóo ha <ha> sido el alumno aventajado